![](https://github.com/bigdata-icict/ETL-Dataiku-DSS/raw/master/tutoriais/pcdas_1.5.png)

# Notebook para criação de tabela de indicadores da PNS - S 2013 Pré-natal - Parte 4

## Bibliotecas Utilizadas

In [ ]:
#Lendo pacotes necessários
library(survey)
library(ggplot2)
library(dplyr)
library(foreign)
library(forcats)
library(tidyverse)
source("utils.R")

## Carregando microdados da PNS

In [2]:
#Carregando banco de dados para R versão 3.5.0 ou superior
load("<coloque aqui o caminho para o arquivo dos microdados formato RDATA PNS 2013>")

#conferindo as dimensões (número de linhas e colunas)
dim("<Coloque aqui o nome do arquivo RDATA PNS 2013>")

[1] 222385   1000

## Definição do peso e filtragem de respondentes do questionário

In [3]:
#Selecionando registros válidos para o módulo K e calculando peso amostral - summary de verificação
pns2013.1<- <Coloque aqui o nome do arquivo RDATA> %>% filter(M001==1) 
pns2013.1<-pns2013.1 %>% mutate(peso_morador_selec=((V00291*(60202/145572211))))
pns2013.1<-pns2013.1 %>% filter(!is.na(peso_morador_selec))
summary(pns2013.1$peso_morador_selec)

     Min.   1st Qu.    Median      Mean   3rd Qu.      Max. 
 0.004156  0.243959  0.521557  1.000000  1.147413 31.179597 

## Criação de variáveis dos indicadores

In [4]:
# Desfechos - Indicadores

# 16. Proporção de mulheres que fizeram teste de HIV/AIDS durante o pré-natal - S016P.
pns2013.1$S016P <- NA
pns2013.1$S016P[pns2013.1$C006==2 & pns2013.1$C008>=18 & pns2013.1$S001==1] <- 2
pns2013.1$S016P[pns2013.1$C006==2 & pns2013.1$C008>=18 & pns2013.1$S001==1 & pns2013.1$S034==1] <- 1
pns2013.1$S016P<-factor(pns2013.1$S016P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2013.1$S016P)


# 18. Proporção de mulheres que receberam indicação da maternidade para o parto durante o pré-natal - S018P.
pns2013.1$S018P <- NA
pns2013.1$S018P[pns2013.1$C006==2 & pns2013.1$C008>=18 & pns2013.1$S001==1] <- 2
pns2013.1$S018P[pns2013.1$C006==2 & pns2013.1$C008>=18 & pns2013.1$S001==1 & pns2013.1$S012 == 1 ] <- 1
pns2013.1$S018P<-factor(pns2013.1$S018P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2013.1$S018P)

# 19. Proporção de mulheres que foram atendidas por médico no último parto - S019P.
pns2013.1$S019P <- NA
pns2013.1$S019P[pns2013.1$C006==2 & pns2013.1$C008>=18 & pns2013.1$S001 > 0] <- 2
pns2013.1$S019P[pns2013.1$C006==2 & pns2013.1$C008>=18 & pns2013.1$S001 > 0 & pns2013.1$S046 == 1] <- 1
pns2013.1$S019P<-factor(pns2013.1$S019P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2013.1$S019P)


Sim   Não  NA's 
 1590   261 58351

Sim   Não  NA's 
 1362   489 58351

Sim   Não  NA's 
 1664   254 58284

## Definições de abrangências

### Situação urbana ou rural

In [5]:
#Situação Urbano ou Rural
pns2013.1 <- pns2013.1 %>% mutate(urb_rur=V0026)
pns2013.1$urb_rur<-factor(pns2013.1$urb_rur, levels=c(1,2), labels=c("urbano", "rural"))
summary(pns2013.1$urb_rur)

urbano  rural 
 49245  10957

### UF

In [6]:
#Estados - UFs
pns2013.1 <- pns2013.1 %>% mutate(uf=V0001)
pns2013.1$uf<-factor(pns2013.1$uf, levels=c(11,12,13,14,15,16,17,21,22,23,24,25,26,27,28,29,31,32,33,35,41,42,43,50,51,52,53),
                     label=c("Rondônia","Acre","Amazonas","Roraima","Pará","Amapá","Tocantins","Maranhão","Piauí","Ceará",
                             "Rio Grande do Norte","Paraíba","Pernambuco","Alagoas","Sergipe","Bahia",
                             "Minas Gerais","Espírito Santo","Rio de Janeiro","São Paulo",
                             "Paraná","Santa Catarina","Rio Grande do Sul", 
                             "Mato Grosso do Sul","Mato Grosso","Goiás","Distrito Federal"))
summary(pns2013.1$uf)

Rondônia                Acre            Amazonas             Roraima 
               1694                1814                2586                1591 
               Pará               Amapá           Tocantins            Maranhão 
               2004                1332                1515                1774 
              Piauí               Ceará Rio Grande do Norte             Paraíba 
               1804                2560                1691                1943 
         Pernambuco             Alagoas             Sergipe               Bahia 
               2591                1748                1553                2641 
       Minas Gerais      Espírito Santo      Rio de Janeiro           São Paulo 
               3779                1724                3486                5305 
             Paraná      Santa Catarina   Rio Grande do Sul  Mato Grosso do Sul 
               3012                1623                2913                1809 
        Mato Grosso               Goiás    Distrito Federal 
               1476                2423                1811

### Grandes Regiões

In [7]:
#Grandes Regiões
pns2013.1 <- pns2013.1 %>% mutate(
    região = fct_collapse(uf,
                          `Norte` = c("Rondônia","Acre","Amazonas","Roraima","Pará", "Amapá","Tocantins"),
                          `Nordeste` = c("Maranhão", "Piauí", "Ceará", "Rio Grande do Norte", "Paraíba","Pernambuco", "Alagoas","Sergipe","Bahia"),
                          `Sudeste` = c("Minas Gerais", "Espírito Santo","Rio de Janeiro", "São Paulo"), 
                          `Sul` = c("Paraná", "Santa Catarina", "Rio Grande do Sul"),
                          `Centro-Oeste`= c("Mato Grosso do Sul","Mato Grosso", "Goiás", "Distrito Federal"))
    )
summary(pns2013.1$região)

Norte     Nordeste      Sudeste          Sul Centro-Oeste 
       12536        18305        14294         7548         7519

### Capital

In [8]:
#Capital
pns2013.1<- pns2013.1 %>% mutate(capital= fct_collapse(uf,
                                        `Porto Velho`= "Rondônia", 
                                        `Boa Vista`= "Roraima",              
                                        `Rio Branco`= "Acre", 
                                        `Manaus` = "Amazonas",
                                        `Belém` = "Pará" ,
                                        `Macapá`= "Amapá",
                                        `Palmas` = "Tocantins",
                                        `São Luís` = "Maranhão",
                                        `Teresina`= "Piauí" ,
                                        `Fortaleza`= "Ceará",
                                        `Natal`= "Rio Grande do Norte",
                                        `João Pessoa`= "Paraíba",
                                        `Recife`= "Pernambuco",
                                        `Maceió`= "Alagoas",
                                        `Aracaju`= "Sergipe",
                                        `Salvador`= "Bahia",
                                        `Belo Horizonte`= "Minas Gerais",
                                        `Vitória`= "Espírito Santo",
                                        `Rio de Janeiro`= "Rio de Janeiro",
                                        `São Paulo`= "São Paulo",
                                        `Curitiba`= "Paraná",
                                        `Florianópolis`= "Santa Catarina",
                                        `Porto Alegre`= "Rio Grande do Sul",
                                        `Campo Grande`=  "Mato Grosso do Sul",
                                        `Cuiabá`= "Mato Grosso",
                                        `Goiânia` = "Goiás",
                                        `Brasília`= "Distrito Federal"))
summary(pns2013.1$capital)

Porto Velho     Rio Branco         Manaus      Boa Vista          Belém 
          1694           1814           2586           1591           2004 
        Macapá         Palmas       São Luís       Teresina      Fortaleza 
          1332           1515           1774           1804           2560 
         Natal    João Pessoa         Recife         Maceió        Aracaju 
          1691           1943           2591           1748           1553 
      Salvador Belo Horizonte        Vitória Rio de Janeiro      São Paulo 
          2641           3779           1724           3486           5305 
      Curitiba  Florianópolis   Porto Alegre   Campo Grande         Cuiabá 
          3012           1623           2913           1809           1476 
       Goiânia       Brasília 
          2423           1811

### Faixa Etária

In [9]:
# Faixas Etárias
pns2013.1 <- pns2013.1 %>% mutate(fx_idade_S=cut(C008,
  breaks = c(18,25,30,40,120),
  labels = c("18 a 24 anos", "25 a 29 anos", "30 a 39 anos", "40 anos ou mais"), 
  ordered_result = TRUE, right = FALSE))
summary(pns2013.1$fx_idade_S)

18 a 24 anos    25 a 29 anos    30 a 39 anos 40 anos ou mais 
           7823            6498           14269           31612

### Raça

In [10]:
# Raça
pns2013.1 <- pns2013.1 %>% mutate(raça= ifelse(C009==1, 1, 
                                               ifelse(C009==2, 2, 
                                                      ifelse(C009==4, 3, 9))))
pns2013.1$raça<-factor(pns2013.1$raça, levels=c(1,2,3),labels=c("Branca", "Preta", "Parda"))
summary(pns2013.1$raça)

Branca  Preta  Parda   NA's 
 24106   5631  29512    953

### Renda per capita

In [11]:
# Rendimento domiciliar per capita
pns2013.1 <-  pns2013.1 %>% mutate(rend_per_capita=cut(VDF003,
  breaks = c(-Inf,339, 678, 1356, 2034, Inf),
  labels=c("Até 1/2 SM","1/2 até 1 SM","1 até 2 SM","2 até 3 SM","Mais de 3 SM"), 
  ordered_result = TRUE, right = TRUE, na.exclude= TRUE))
summary(pns2013.1$rend_per_capita)

Até 1/2 SM 1/2 até 1 SM   1 até 2 SM   2 até 3 SM Mais de 3 SM         NA's 
       14256        17504        15493         5335         7603           11

### Escolaridade

In [12]:
# Escolaridade
pns2013.1 <- pns2013.1 %>% mutate(gescol = ifelse(VDD004A %in% 1:2, 1, 
                        ifelse(VDD004A%in% 3:4, 2, 
                        ifelse(VDD004A%in% 5:6, 3,4
                        ))))
pns2013.1$gescol<-factor(pns2013.1$gescol, levels=c(1,2,3,4), 
                                  labels=c("Fundamental incompleto ou equivalente","Médio incompleto ou equivalente",
                                           "Superior incompleto ou equivalente","Superior completo"))

summary(pns2013.1$gescol)

Fundamental incompleto ou equivalente       Médio incompleto ou equivalente 
                                24083                                  9215 
   Superior incompleto ou equivalente                     Superior completo 
                                19149                                  7755

## Criando indicadores

### Filtrando base de indicadores

In [13]:
# Selecionando variáveis para cálculo de indicadores no survey
pns2013Ssurvey<- pns2013.1 %>% select("V0024","UPA_PNS","peso_morador_selec",  "C008", "C006", "C009", "V0031",
                    "urb_rur", "uf", "região",  "capital", "fx_idade_S", "raça",
                    "rend_per_capita", "gescol", "S016P", "S018P", "S019P", "S001")  
summary(pns2013Ssurvey)

     V0024            UPA_PNS        peso_morador_selec       C008       
 Min.   :1110011   Min.   :1100001   Min.   : 0.004156   Min.   : 18.00  
 1st Qu.:2210013   1st Qu.:2200075   1st Qu.: 0.243959   1st Qu.: 30.00  
 Median :2951023   Median :2900192   Median : 0.521557   Median : 41.00  
 Mean   :3035353   Mean   :3007819   Mean   : 1.000000   Mean   : 43.31  
 3rd Qu.:4110111   3rd Qu.:4100002   3rd Qu.: 1.147413   3rd Qu.: 55.00  
 Max.   :5310220   Max.   :5300180   Max.   :31.179597   Max.   :101.00  
                                                                         
      C006            C009          V0031         urb_rur     
 Min.   :1.000   Min.   :1.00   Min.   :1.000   urbano:49245  
 1st Qu.:1.000   1st Qu.:1.00   1st Qu.:1.000   rural :10957  
 Median :2.000   Median :3.00   Median :2.000                 
 Mean   :1.569   Mean   :2.61   Mean   :2.308                 
 3rd Qu.:2.000   3rd Qu.:4.00   3rd Qu.:4.000                 
 Max.   :2.000   Max.   :9.00 

### Exporta tabela filtrada com os dados específicos - Módulo S - Parte 4 2013

In [14]:
# Salvando csv para cálculo de indicadores no survey
diretorio_saida <- "<coloque aqui o diretório>"
write.csv(pns2013Ssurvey, file.path(diretorio_saida, "pns2013Ssurvey.csv"))

### Cria plano amostral complexo

In [15]:
# survey design
desPNS=svydesign(id=~UPA_PNS, 
                 strat=~V0024,
                 weight=~peso_morador_selec,
                 nest=TRUE,
                 data=pns2013Ssurvey)

In [16]:
#survey design S016P, S018P
desPNSS=subset(desPNS,   C006==2 & C008>=18 & S001==1)
desPNSS_C=subset(desPNS, C006==2 & C008>=18 & S001==1 & V0031==1)
desPNSS_R=subset(desPNS, C006==2 & C008>=18 & S001==1 & !is.na(raça))
desPNSS_Rend=subset(desPNS, C006==2 & C008>=18 & S001==1 & !is.na(rend_per_capita))

In [17]:
#survey design S019P
desPNSS_S019P=subset(desPNS,   C006==2 & C008>=18 & S001>0)
desPNSS_S019P_C=subset(desPNS, C006==2 & C008>=18 & S001>0 & V0031==1)
desPNSS_S019P_R=subset(desPNS, C006==2 & C008>=18 & S001>0 & !is.na(raça))
desPNSS_S019P_Rend=subset(desPNS, C006==2 & C008>=18 & S001>0 & !is.na(rend_per_capita))

### Criação da tabela de indicadores
Essa tabela é responsável por unir os indicadores no formato do painel de indicadores

#### Definição de variáveis para iteração dos indicadores

In [18]:
design_por_abrangencia <- list(
    S016P = list(
        capital = desPNSS_C,
        raça = desPNSS_R,
        rend_per_capita = desPNSS_Rend,
        default = desPNSS
    ),
    S018P = list(
        capital = desPNSS_C,
        raça = desPNSS_R,
        rend_per_capita = desPNSS_Rend,
        default = desPNSS
    ),
    S019P = list(
        capital = desPNSS_S019P_C,
        raça = desPNSS_S019P_R,
        rend_per_capita = desPNSS_S019P_Rend,
        default = desPNSS_S019P
    )
)
dominios <- c(
    ~raça,
    ~rend_per_capita,
    ~fx_idade_S,
    ~urb_rur,
    ~uf,
    ~região,
    ~capital,
    ~gescol
) 
indicadores <- c(~S016P, ~S018P, ~S019P)
totais <- c(~Brasil,~Capital)
Ano <- "2013"

#### Preenchendo a tabela de indicadores

In [19]:
matriz_indicadores <- popula_indicadores(design_por_abrangencia, dominios, indicadores, Ano)

In [20]:
matriz_indicadores

abr_tipo       
Branca                                 raça           
Preta                                  raça           
Parda                                  raça           
Até 1/2 SM                             rend_per_capita
1/2 até 1 SM                           rend_per_capita
1 até 2 SM                             rend_per_capita
2 até 3 SM                             rend_per_capita
Mais de 3 SM                           rend_per_capita
18 a 24 anos                           fx_idade_s     
25 a 29 anos                           fx_idade_s     
30 a 39 anos                           fx_idade_s     
40 anos ou mais                        fx_idade_s     
urbano                                 urb_rur        
rural                                  urb_rur        
Rondônia                               uf             
Acre                                   uf             
Amazonas                               uf             
Roraima                                uf             
Pará                                   uf             
Amapá                                  uf             
Tocantins                              uf             
Maranhão                               uf             
Piauí                                  uf             
Ceará                                  uf             
Rio Grande do Norte                    uf             
Paraíba                                uf             
Pernambuco                             uf             
Alagoas                                uf             
Sergipe                                uf             
Bahia                                  uf             
⋮                                      ⋮              
Rio Branco2                            capital        
Manaus2                                capital        
Boa Vista2                             capital        
Belém2                                 capital        
Macapá2                                capital        
Palmas2                                capital        
São Luís2                              capital        
Teresina2                              capital        
Fortaleza2                             capital        
Natal2                                 capital        
João Pessoa2                           capital        
Recife2                                capital        
Maceió2                                capital        
Aracaju2                               capital        
Salvador2                              capital        
Belo Horizonte2                        capital        
Vitória2                               capital        
Rio de Janeiro5                        capital        
São Paulo4                             capital        
Curitiba2                              capital        
Florianópolis2                         capital        
Porto Alegre2                          capital        
Campo Grande2                          capital        
Cuiabá2                                capital        
Goiânia2                               capital        
Brasília2                              capital        
Fundamental incompleto ou equivalente2 gescol         
Médio incompleto ou equivalente2       gescol         
Superior incompleto ou equivalente2    gescol         
Superior completo2                     gescol         
                                       abr_nome                             
Branca                                 Branca                               
Preta                                  Preta                                
Parda                                  Parda                                
Até 1/2 SM                             Até 1/2 SM                           
1/2 até 1 SM                           1/2 até 1 SM                         
1 até 2 SM                             1 até 2 SM                           
2 até 3 SM                             2 até 3 SM                           
Mais de 3 SM 

#### Preenchendo a tabela pela abrangência total

In [21]:
matriz_totais <- popula_indicadores(design_por_abrangencia, totais, indicadores, Ano, "total")

In [22]:
matriz_totais

abr_tipo abr_nome Ano  Indicador Sim       LowerS    UpperS   
S016PSim  total    Brasil   2013 S016P     0.8509319 0.8234418 0.8784220
S016PSim1 total    Capital  2013 S016P     0.8947766 0.8621891 0.9273641
S018PSim  total    Brasil   2013 S018P     0.7514091 0.7184669 0.7843514
S018PSim1 total    Capital  2013 S018P     0.8049977 0.7689407 0.8410546
S019PSim  total    Brasil   2013 S019P     0.8763847 0.8526117 0.9001576
S019PSim1 total    Capital  2013 S019P     0.9166140 0.8907343 0.9424937
          cvS       
S016PSim  0.01648289
S016PSim1 0.01858181
S018PSim  0.02236807
S018PSim1 0.02285318
S019PSim  0.01384011
S019PSim1 0.01440536

#### Unindo tabela de indicadores e de totais

In [23]:
matriz_final <-rbind(matriz_indicadores,matriz_totais)

#### Visualizando tabela de indicadores

In [24]:
matriz_final

abr_tipo       
Branca                                 raça           
Preta                                  raça           
Parda                                  raça           
Até 1/2 SM                             rend_per_capita
1/2 até 1 SM                           rend_per_capita
1 até 2 SM                             rend_per_capita
2 até 3 SM                             rend_per_capita
Mais de 3 SM                           rend_per_capita
18 a 24 anos                           fx_idade_s     
25 a 29 anos                           fx_idade_s     
30 a 39 anos                           fx_idade_s     
40 anos ou mais                        fx_idade_s     
urbano                                 urb_rur        
rural                                  urb_rur        
Rondônia                               uf             
Acre                                   uf             
Amazonas                               uf             
Roraima                                uf             
Pará                                   uf             
Amapá                                  uf             
Tocantins                              uf             
Maranhão                               uf             
Piauí                                  uf             
Ceará                                  uf             
Rio Grande do Norte                    uf             
Paraíba                                uf             
Pernambuco                             uf             
Alagoas                                uf             
Sergipe                                uf             
Bahia                                  uf             
⋮                                      ⋮              
São Luís2                              capital        
Teresina2                              capital        
Fortaleza2                             capital        
Natal2                                 capital        
João Pessoa2                           capital        
Recife2                                capital        
Maceió2                                capital        
Aracaju2                               capital        
Salvador2                              capital        
Belo Horizonte2                        capital        
Vitória2                               capital        
Rio de Janeiro5                        capital        
São Paulo4                             capital        
Curitiba2                              capital        
Florianópolis2                         capital        
Porto Alegre2                          capital        
Campo Grande2                          capital        
Cuiabá2                                capital        
Goiânia2                               capital        
Brasília2                              capital        
Fundamental incompleto ou equivalente2 gescol         
Médio incompleto ou equivalente2       gescol         
Superior incompleto ou equivalente2    gescol         
Superior completo2                     gescol         
S016PSim                               total          
S016PSim1                              total          
S018PSim                               total          
S018PSim1                              total          
S019PSim                               total          
S019PSim1                              total          
                                       abr_nome                             
Branca                                 Branca                               
Preta                                  Preta                                
Parda                                  Parda                                
Até 1/2 SM                             Até 1/2 SM                           
1/2 até 1 SM                           1/2 até 1 SM                         
1 até 2 SM                             1 até 2 SM                           
2 até 3 SM                             2 até 3 SM                           
Mais de 3 SM 

#### Exportando tabela de indicadores calculados - Módulo S 2013

In [26]:
diretorio_saida <- "<coloque aqui o diretório>"
write.table(matrizIndicadores,file=paste0(diretorio_saida,"Indicadores_2013S_R.csv"),sep = ";",dec = ",",row.names = FALSE)